In [ ]:
!pip3 install pyvista
!pip3 install panel
!pip3 install pyacvd

In [2]:
#Importing necessary dependencies
import pyvista as pv
import panel
import statistics 
import matplotlib.pyplot as plt
import numpy as np
import pyacvd
from pyacvd import Clustering
from vtkmodules.vtkCommonDataModel import vtkIterativeClosestPointTransform
pv.set_plot_theme('document')
pv.global_theme.jupyter_backend = 'panel'

/var/folders/1g/ltjd_qkj2msdclkpc1lj9rb40000gn/T/ipykernel_20955/2463167042.py:11: PyVistaDeprecationWarning: `panel` backend is deprecated and is planned for future removal.
  pv.global_theme.jupyter_backend = 'panel'


In [3]:
#this is our ideal mesh created manually in Autodesk MeshMixer
meanmesh = pv.read('~/Desktop/knee-mesh-processing/MeanMesh/ACLC_mean_Femur_Cartilage.stl')

In [4]:
#PLOTTING meanmesh and printing its number of faces 
meanmesh.plot()
print(meanmesh.n_faces)

2023-05-02 17:53:54.393 Python[20955:2358588] ApplePersistenceIgnoreState: Existing state will not be touched. New state will be written to /var/folders/1g/ltjd_qkj2msdclkpc1lj9rb40000gn/T/com.apple.python3.savedState


VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

21791


In [30]:
#Loading the initial mesh as extracted from MRI scans
mesh = pv.read('~/Desktop/knee-mesh-processing/T001_Femur_Cartilage.stl') 

In [31]:
#PLOTTING initial mesh
mesh.plot()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

In [7]:
#Decimating mesh to match ideal number of polygons
target_reduction = 1 - (meanmesh.n_faces / mesh.n_faces) #0.86104805387
decimated = mesh.decimate(target_reduction)

In [8]:
#PLOTTING decimated mesh and comparing 
print("Before:", mesh.n_faces)
print("After:",decimated.n_faces)
decimated.plot()

Before: 111318
After: 21790


VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

In [9]:
# Smoothing the mesh
surf = decimated.extract_geometry()
smooth = surf.smooth(n_iter=1000) #number of iterations parameter can be experimented with

In [10]:
#PLOTTING smoothed mesh
smooth.plot()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

In [11]:
#Decimating Boundaries to remove sharp edges
clean = smooth
reduction = 0.9
clean = clean.decimate_boundary(reduction)
clean = clean.smooth(100)

In [12]:
#PLOTTING cleaned boundary mesh and comparing number of faces after 2nd round of decimation 
print("before:", smooth.n_faces)
print("after:", clean.n_faces)
clean.plot()

before: 21790
after: 2178


VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

In [13]:
#Ray Tracing step to remove inside surface of the mesh
traced = clean
start = traced.center #our ray starting point will be the predefined center of the mesh
stop = traced.points #our ray stopping points will be every point in the mesh
points = [] #storing point and cell intersection for each ray 
incells = [] 
for s in stop:
    point, cell = traced.ray_trace(start, s, first_point=True) #taking the first intersection point and cell of each ray 
    points.append(point) 
    incells.append(cell)
intersection = pv.PolyData(points)

In [14]:
#PLOTTING the lines to demonstrate the ray tracing (this code block can be excluded to speed up processing)
rays = [pv.Line(start, stop) for stop in stop] #creating a new line mesh to plot the ray tracing 
p = pv.Plotter(off_screen=True)
p.add_mesh(traced, show_edges=True, opacity=0.5, color="w", lighting=False, label="Test Mesh")
for r in rays:
    p.add_mesh(r, color="blue", line_width=5, label="Ray Segment")
p.add_mesh(intersection, color="maroon", point_size=25, label="Intersection Points")
p.show()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, sizing_mode='stretch_width')

In [15]:
#Removing intersection points to remove inside surface of mesh
split = traced
inpoints = [] #points that are in the mesh
for p in intersection.points: #determining which intersection points are points that are part of the mesh rather than cell intersection points
    if p in split.points:
        inpoints.append(p)
        
#the remove_points() function takes an array of point indices not coordinates
removelist = [] #list of point indices 
temp = split
for p in inpoints:
    to_remove = split.find_closest_point(p) #Finding the index of the point in the mesh closest to the intersection point
    if to_remove > -1: #if point is found, append to list 
        removelist.append(to_remove)
        
temp, i = temp.remove_points(removelist, mode='all') #removing the points 

In [16]:
#PLOTTING mesh after remove inside surface, comparing # of points removed
print("total points", len(split.points))
print("removing ", len(removelist))
temp.plot()

total points 1090
removing  563


VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

In [17]:
#Subdividing the mesh using clustering algorithm 
clus = Clustering(temp)
clus.subdivide(4) #Number of subdivisions and clustering can be played with for better results
clus.cluster(5000) 
remesh = clus.create_mesh()

In [18]:
#PLOTTING after remeshing
remesh.plot(smooth_shading=True)
print(remesh.n_faces)

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, orientation_widget=True, sizing_mode='stretch_width')

9613


In [19]:
largest = remesh.connectivity(largest=True)

In [20]:
#PLOTTING large
largest.plot()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, color_mappers=[LinearColorMapper(id='102...], orientation_widget=True, sizing_mode='stretch_width')

In [21]:
#Comparing centers of processed and ideal mesh
print(remesh.center)
print(meanmesh.center)

[-32.34391556572713, 16.65875923571094, 0.6257710255665536]
[0.0013650525361299515, 0.007043853402137756, -0.005683333612978458]


In [22]:
#Translating meshes to match mesh centers 
moved = remesh.translate((meanmesh.center[0]-remesh.center[0], meanmesh.center[1]-remesh.center[1], meanmesh.center[2]-remesh.center[2]))
print(moved.center)

[0.0013650525361335042, 0.007043853402137756, -0.005683333612978458]


In [23]:
#comparing mesh lengths
print(moved.length)
print(meanmesh.length)

95.46006334824807
0.10942365498003416


In [24]:
#Scaling the mesh to match the size of the ideal mesh
scaled = moved.scale((0.001103781597,0.001103781597,0.001103781597), inplace=False)

In [25]:
#Rotating the mesh to line up with the ideal mesh
rotated = scaled.rotate_z(180)

In [26]:
#PLOTTING the aligned meshes 
p = pv.Plotter()
p.add_mesh(rotated, color='red')
p.add_mesh(meanmesh, color='green')
p.show()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, sizing_mode='stretch_width')

In [27]:
#Using Iterative Closest Point algorithm to align the 2 meshes as closely as possible 
icp = vtkIterativeClosestPointTransform()
icp.SetSource(rotated)
icp.SetTarget(meanmesh)
icp.GetLandmarkTransform().SetModeToRigidBody()
icp.SetMaximumNumberOfLandmarks(100)
icp.SetMaximumMeanDistance(.00001)
icp.SetMaximumNumberOfIterations(500)
icp.CheckMeanDistanceOn()
icp.StartByMatchingCentroidsOn()
icp.Update()

aligned = rotated.transform(icp.GetMatrix())

In [28]:
#PLOTTING the aligned meshes 
p = pv.Plotter()
p.add_mesh(aligned, color='red')
p.add_mesh(meanmesh, color='green', opacity=0.5)
p.show()

VTKRenderWindowSynchronized(vtkCocoaRenderWindow, sizing_mode='stretch_width')

In [29]:
#saving mesh stl file
aligned.save("processed_femur_cartilage.stl")